In [3]:
# Importar bibliotecas
import os
import csv
from datetime import datetime

from pymoo.problems import get_problem
from pymoo.algorithms.moo.nsga2 import NSGA2
from pymoo.optimize import minimize
from pymoo.visualization.scatter import Scatter

In [ ]:
import os
from huggingface_hub import login

login(token=os.environ["HF_TOKEN"])

os.environ["DIFFUSERS_BACKEND"] = "torch"

from problema import StableDiffusionProblem

print("¡Autenticación correcta y modelo cargado!")


/root/micromamba/envs/nombre_entorno/lib/python3.12/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm
2026-02-07 19:17:07.413582: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2026-02-07 19:17:07.515980: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2026-02-07 19:17:09.624959: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You ma

Creating new Ultralytics Settings v0.0.6 file ✅ 
View Ultralytics Settings with 'yolo settings' or at '/root/.config/Ultralytics/settings.json'
Update Settings with 'yolo settings key=value', i.e. 'yolo settings runs_dir=path/to/dir'. For help see https://docs.ultralytics.com/quickstart/#ultralytics-settings.


/root/micromamba/envs/nombre_entorno/lib/python3.12/site-packages/torch/amp/autocast_mode.py:265: UserWarning: User provided device_type of 'cuda', but CUDA is not available. Disabling
  warnings.warn(
Couldn't connect to the Hub: 404 Client Error. (Request ID: Root=1-69878fb8-67efc9f6656aad5e0158bb4d;38a9579c-930d-4660-8882-703bcb8595c9)

Repository Not Found for url: https://huggingface.co/api/models/stabilityai/stable-diffusion-2-1.
Please make sure you specified the correct `repo_id` and `repo_type`.
If you are trying to access a private or gated repo, make sure you are authenticated. For more details, see https://huggingface.co/docs/huggingface_hub/authentication.
Will try to load from local cache.


OSError: Cannot load model stabilityai/stable-diffusion-2-1: model is not cached locally and an error occurred while trying to fetch metadata from the Hub. Please check out the root cause in the stacktrace above.

In [ ]:
# --- 1. Librerías Estándar de Python ---
import csv
import datetime
from datetime import datetime
import itertools
import json
import os
import random
import zipfile
from multiprocessing.pool import ThreadPool

# --- 2. Librerías de Ciencia de Datos y Visión (Third-Party) ---
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from PIL import Image

# --- 3. PyTorch y Modelos de ML (Hugging Face / Ultralytics) ---
import torch
from diffusers import StableDiffusionPipeline
from ultralytics import YOLO

# --- 4. Pymoo (Optimización Multi-objetivo) ---
# Core y Optimización
from pymoo.core.problem import Problem
from pymoo.optimize import minimize

# Algoritmos
from pymoo.algorithms.moo.nsga2 import NSGA2
from pymoo.algorithms.moo.sms import SMSEMOA
from pymoo.algorithms.moo.moead import MOEAD

# Terminación (Condiciones de parada)
from pymoo.termination import get_termination
from pymoo.termination.collection import TerminationCollection
from pymoo.termination.default import DefaultMultiObjectiveTermination

# Nota: Si usas tu clase personalizada, recuerda importarla desde tu archivo local o pymoo.core.termination

# Indicadores y Métricas
from pymoo.indicators.hv import Hypervolume
from pymoo.util.nds.non_dominated_sorting import NonDominatedSorting

# Utilidades y Descomposición
from pymoo.decomposition.tchebicheff import Tchebicheff
from pymoo.util.ref_dirs import get_reference_directions
from pymoo.parallelization.starmap import StarmapParallelization

# Visualización
from pymoo.visualization.scatter import Scatter

# --- 5. Módulos Locales (Tu proyecto) ---
from operadores import get_crossover, get_mutation
from problema import StableDiffusionProblem


import logging
import traceback



In [4]:
# Lista de operadores disponibles
crossover_names = ["sbx", "uniform"]
mutation_names = ["polynomial", "gaussian"]

# Generamos todas las combinaciones posibles
combinaciones = list(itertools.product(crossover_names, mutation_names))

# Podemos visualizar qué combinaciones se van a probar
print("Se van a probar las siguientes combinaciones:")
for cx, mut in combinaciones:
    print(f"Crossover: {cx}, Mutación: {mut}")

Se van a probar las siguientes combinaciones:
Crossover: sbx, Mutación: polynomial
Crossover: sbx, Mutación: gaussian
Crossover: uniform, Mutación: polynomial
Crossover: uniform, Mutación: gaussian


In [8]:

def get_termination_custom(
    n_gen,
    ftol=1e-4,       # tolerancia en espacio objetivo (CLAVE)
    period=5,        # cada cuántas generaciones comprobar
    n_max_evals=100000
):
    return DefaultMultiObjectiveTermination(
        xtol=1e-8,          # normalmente no es el criterio dominante
        cvtol=1e-6,         # irrelevante si no hay constraints
        ftol=ftol,          # <-- activa parada por convergencia
        period=period,
        n_max_gen=n_gen,    # límite duro
        n_max_evals=n_max_evals
    )

In [ ]:

# =========================
# CONFIG GLOBAL
# =========================
OUTPUT_DIR = "TFG/SMSEMOA"
os.makedirs(OUTPUT_DIR, exist_ok=True)

RUNS_SUMMARY_PATH = os.path.join(OUTPUT_DIR, "runs_summary.csv")
FRONT_FINAL_PATH  = os.path.join(OUTPUT_DIR, "front_final.csv")
HISTORY_PATH      = os.path.join(OUTPUT_DIR, "history.csv")

REF_POINT_HV = [0.0, 80]

HV_INVERT_OBJ1 = False

In [ ]:




# =========================
# HELPERS (todas estas funciones tienen que ir a utils.py)
# =========================
def _ensure_header(path: str, fieldnames: list[str]) -> None:
    """Create CSV with header if it doesn't exist yet."""
    if not os.path.isfile(path):
        with open(path, mode="w", newline="", encoding="utf-8") as f:
            w = csv.DictWriter(f, fieldnames=fieldnames)
            w.writeheader()

def _append_row(path: str, row: dict, fieldnames: list[str]) -> None:
    """Append a row using stable field order."""
    _ensure_header(path, fieldnames)
    with open(path, mode="a", newline="", encoding="utf-8") as f:
        w = csv.DictWriter(f, fieldnames=fieldnames)
        w.writerow({k: row.get(k, None) for k in fieldnames})

def _write_rows(path: str, rows: list[dict], fieldnames: list[str]) -> None:
    _ensure_header(path, fieldnames)
    with open(path, mode="a", newline="", encoding="utf-8") as f:
        w = csv.DictWriter(f, fieldnames=fieldnames)
        for row in rows:
            w.writerow({k: row.get(k, None) for k in fieldnames})



PARETO_DIR = os.path.join(OUTPUT_DIR, "paretos")
os.makedirs(PARETO_DIR, exist_ok=True)

def save_pareto(res, experiment_id: str) -> str | None:
    pop = getattr(res, "pop", None)
    if pop is None:
        return None

    X = pop.get("X")
    F = pop.get("F")
    G = pop.get("G")   # <-- clave (restricciones)

    if X is None or F is None:
        return None

    X = np.asarray(X)
    F = np.asarray(F)

    if X.size == 0 or F.size == 0:
        return None

    # Si hay restricciones, filtrar factibles
    if G is not None:
        G = np.asarray(G)
        feasible = np.all(G <= 0, axis=1)
        X = X[feasible]
        F = F[feasible]

    # Si tras filtrar no quedan, no hay Pareto factible
    if F.shape[0] == 0:
        print("[save_pareto] No hay soluciones factibles (YOLO>=0.1) en la población final.")
        return None

    # ND-front dentro del conjunto factible
    nd_idx = NonDominatedSorting().do(F, only_non_dominated_front=True)

    X_nd = X[nd_idx]
    F_nd = F[nd_idx]

    columns_X = ["iterations", "cfg", "sd_seed", "guidance_rescale"]
    columns_F = ["f1_alg", "f2"]

    pareto_df = pd.DataFrame(np.hstack((X_nd, F_nd)), columns=columns_X + columns_F)
    pareto_df["fitness_yolo"] = -pareto_df["f1_alg"]

    out_csv = os.path.join(PARETO_DIR, f"pareto_{experiment_id}.csv")
    pareto_df.to_csv(out_csv, index=False)

    print(f"[save_pareto] pareto_factible_size={len(nd_idx)}")
    return out_csv



def _safe_float(x):
    try:
        return float(x)
    except Exception:
        return None

def _safe_int(x):
    try:
        return int(x)
    except Exception:
        return None

In [10]:
# -------------------------
# RUN SUMMARY CSV (1 fila por run, SIN best)
# -------------------------
def save_run_summary(
    algorithm_name: str,  
    experiment_id: str,
    run_id: int,
    crossover_name: str,
    mutation_name: str,
    pop_size: int,
    n_gen_max: int,
    res,
    hv_value,
) -> None:

    n_gen_real = getattr(res.algorithm, "n_gen", None)
    n_gen_real = int(n_gen_real) if n_gen_real is not None else None

    pop_final = res.pop
    F_final = np.asarray(pop_final.get("F"))
    G_final = pop_final.get("G")

    n_final_pop = int(F_final.shape[0])

    # filtra factibles para stats agregadas (coherente con HV y Pareto)
    if G_final is not None:
        G_final = np.asarray(G_final)
        feas = np.all(G_final <= 0, axis=1)
        F_use = F_final[feas]
    else:
        F_use = F_final

    n_feasible_final = int(F_use.shape[0])

    f1_min = float(np.min(F_use[:, 0])) if n_feasible_final > 0 else None
    f1_mean = float(np.mean(F_use[:, 0])) if n_feasible_final > 0 else None
    f2_min = float(np.min(F_use[:, 1])) if n_feasible_final > 0 else None
    f2_mean = float(np.mean(F_use[:, 1])) if n_feasible_final > 0 else None

    fitness_yolo_max = float(np.max(-F_use[:, 0])) if n_feasible_final > 0 else None
    fitness_yolo_mean = float(np.mean(-F_use[:, 0])) if n_feasible_final > 0 else None

    row = {
        "experiment_id": experiment_id,
        "algorithm": algorithm_name, 
        "crossover": crossover_name,
        "mutation": mutation_name,
        "run_id": run_id,
        "timestamp": datetime.now().isoformat(),

        "pop_size": pop_size,
        "n_gen_max": n_gen_max,
        "n_gen_real": n_gen_real,

        "n_final_pop": n_final_pop,
        "n_feasible_final": n_feasible_final,

        "f1_min_feas": f1_min,
        "f1_mean_feas": f1_mean,
        "f2_min_feas": f2_min,
        "f2_mean_feas": f2_mean,

        "fitness_yolo_max_feas": fitness_yolo_max,
        "fitness_yolo_mean_feas": fitness_yolo_mean,

        "ref_point_hv": json.dumps(REF_POINT_HV),
        "hypervolume_feas": hv_value,
    }

    fieldnames = [
        "experiment_id","algorithm","crossover","mutation","run_id","timestamp",
        "pop_size","n_gen_max","n_gen_real",
        "n_final_pop","n_feasible_final",
        "f1_min_feas","f1_mean_feas","f2_min_feas","f2_mean_feas",
        "fitness_yolo_max_feas","fitness_yolo_mean_feas",
        "ref_point_hv","hypervolume_feas"
    ]

    _append_row(RUNS_SUMMARY_PATH, row, fieldnames)


    
def save_history_csv(res, experiment_id: str, run_id: int) -> None:
    if not hasattr(res, "history") or res.history is None:
        return

    rows = []
    hv_ref = np.array(REF_POINT_HV, dtype=float)

    for gen_idx, hist in enumerate(res.history):
        pop = hist.pop
        Fg = np.asarray(pop.get("F"))
        Gg = pop.get("G")
        n_pop = int(Fg.shape[0])

        if Gg is not None:
            Gg = np.asarray(Gg)
            feas = np.all(Gg <= 0, axis=1)
            F_use = Fg[feas]
        else:
            feas = np.ones(n_pop, dtype=bool)
            F_use = Fg

        n_feas = int(np.sum(feas))

        hv_g = Hypervolume(ref_point=hv_ref)
        hv_val = float(hv_g.do(F_use)) if F_use.shape[0] > 0 else None

        if F_use.shape[0] > 0:
            f1_min = float(np.min(F_use[:, 0]))
            f2_min = float(np.min(F_use[:, 1]))
            f1_mean = float(np.mean(F_use[:, 0]))
            f2_mean = float(np.mean(F_use[:, 1]))
            fitness_yolo_max = float(np.max(-F_use[:, 0]))
            fitness_yolo_mean = float(np.mean(-F_use[:, 0]))
        else:
            f1_min = f2_min = f1_mean = f2_mean = None
            fitness_yolo_max = fitness_yolo_mean = None

        rows.append({
            "experiment_id": experiment_id,
            "run_id": run_id,
            "gen": int(gen_idx),
            "n_pop": n_pop,
            "n_feasible": n_feas,
            "f1_min_feas": f1_min,
            "f2_min_feas": f2_min,
            "f1_mean_feas": f1_mean,
            "f2_mean_feas": f2_mean,
            "fitness_yolo_max_feas": fitness_yolo_max,
            "fitness_yolo_mean_feas": fitness_yolo_mean,
            "ref_point_hv": json.dumps(REF_POINT_HV),
            "hypervolume_feas": hv_val,
        })

    fieldnames = [
        "experiment_id","run_id","gen",
        "n_pop","n_feasible",
        "f1_min_feas","f2_min_feas","f1_mean_feas","f2_mean_feas",
        "fitness_yolo_max_feas","fitness_yolo_mean_feas",
        "ref_point_hv","hypervolume_feas"
    ]
    _write_rows(HISTORY_PATH, rows, fieldnames)

# ==================
# error log csv
# ==================

RUNS_ERRORS_PATH = os.path.join(OUTPUT_DIR, "runs_errors.csv")
LOG_PATH = os.path.join(OUTPUT_DIR, "runs.log")

def setup_logger():
    logger = logging.getLogger("tfg_runs")
    logger.setLevel(logging.INFO)

    # evita handlers duplicados en notebooks
    if not any(isinstance(h, logging.FileHandler) and h.baseFilename == os.path.abspath(LOG_PATH)
               for h in logger.handlers):

        fh = logging.FileHandler(LOG_PATH, encoding="utf-8")
        fh.setLevel(logging.INFO)
        fmt = logging.Formatter("%(asctime)s | %(levelname)s | %(message)s")
        fh.setFormatter(fmt)
        logger.addHandler(fh)

    return logger

LOGGER = setup_logger()


def save_run_error(experiment_id: str, run_id: int, algorithm_name: str, crossover: str, mutation: str, err: Exception):
    row = {
        "experiment_id": experiment_id,
        "run_id": run_id,
        "algorithm": algorithm_name,
        "crossover": crossover,
        "mutation": mutation,
        "timestamp": datetime.now().isoformat(),
        "error_type": type(err).__name__,
        "error_msg": str(err),
        "traceback": traceback.format_exc(),
    }
    fieldnames = ["experiment_id","run_id","algorithm","crossover","mutation","timestamp","error_type","error_msg","traceback"]
    _append_row(RUNS_ERRORS_PATH, row, fieldnames)



In [ ]:
from pymoo.core.callback import Callback


import logging
logging.getLogger("diffusers").setLevel(logging.ERROR)
logging.getLogger("transformers").setLevel(logging.ERROR)

# opcional: si tu pipe es de diffusers:
try:
    pipe.set_progress_bar_config(disable=True)
except Exception:
    pass

class RunProgressCallback(Callback):
    def __init__(self, experiment_id: str, log_every: int = 1):
        super().__init__()
        self.experiment_id = experiment_id
        self.log_every = log_every

    def notify(self, algorithm):
        # se llama cada generación
        gen = int(getattr(algorithm, "n_gen", -1))

        if self.log_every > 1 and (gen % self.log_every != 0):
            return

        pop = algorithm.pop
        if pop is None:
            return

        F = pop.get("F")
        G = pop.get("G")

        n_pop = len(pop) if pop is not None else 0
        n_feas = None

        if G is not None:
            G = np.asarray(G)
            feas = np.all(G <= 0, axis=1)
            n_feas = int(np.sum(feas))

        LOGGER.info(
            f"[{self.experiment_id}] gen={gen} pop={n_pop}"
            + (f" feas={n_feas}" if n_feas is not None else "")
        )


# =========================
# MAIN
# =========================
def ejecutar_experimento(
    genetico: str,
    crossover_name: str,
    mutation_name: str,
    run_id: int,
    n_gen: int = 100,
    pop_size: int = 20,
    n_workers: int = 2,
    save_images: bool = False,
    crossover_prob: float = 0.9,
    crossover_eta: float = 15.0,
    mutation_prob: float = 0.2,
    mutation_eta: float = 20.0,
    mutation_sigma: float = 0.1,
):
    experiment_id = f"{genetico}_{crossover_name}_{mutation_name}_run{run_id:02d}"
    genetico_norm = genetico.strip().lower()

    if genetico_norm not in {"nsga2", "moead", "smsemoa"}:
        raise ValueError("genetico debe ser 'nsga2', 'moead' o 'smsemoa'")

    LOGGER.info(f"[START] {experiment_id} pop={pop_size} n_gen={n_gen} workers={n_workers} save_images={save_images}")
    print(f"\nEjecutando: {experiment_id} |  pop={pop_size} | n_gen={n_gen}")

    pool = ThreadPool(n_workers)
    runner = StarmapParallelization(pool.starmap)

    try:
        # IMPORTANTE: pasa runner al Problem (como ya haces)
        problem = StableDiffusionProblem(elementwise_runner=runner, save_images=save_images)

        crossover = get_crossover(crossover_name, prob=crossover_prob, eta=crossover_eta)
        mutation  = get_mutation(mutation_name, prob=mutation_prob, eta=mutation_eta, sigma=mutation_sigma)

        if genetico_norm == "nsga2":
            algorithm = NSGA2(pop_size=pop_size, crossover=crossover, mutation=mutation)

        elif genetico_norm == "moead":
            algorithm = MOEAD(
                pop_size=pop_size,
                n_neighbors=moead_n_neighbors,
                decomposition=decomposition,
                crossover=crossover,
                mutation=mutation
            )

        else:  # smsemoa
            algorithm = SMSEMOA(
                pop_size=pop_size,
                ref_point=np.array(REF_POINT_HV, dtype=float),
                crossover=crossover,
                mutation=mutation,
            )

        termination = get_termination_custom(n_gen=n_gen, ftol=1e-4, period=5)

        callback = RunProgressCallback(experiment_id, log_every=1)

        res = minimize(
            problem,
            algorithm,
            termination,
            verbose=False,
            save_history=True,
            callback=callback
        )

        # ---- post: factibles
        pop_final = res.pop
        F_final = np.asarray(pop_final.get("F"))
        G_final = pop_final.get("G")

        if G_final is not None:
            G_final = np.asarray(G_final)
            feasible = np.all(G_final <= 0, axis=1)
            F_feas = F_final[feasible]
        else:
            F_feas = F_final

        pareto_path = save_pareto(res, experiment_id)
        if pareto_path:
            print(f"Pareto CSV -> {pareto_path}")

        hv = Hypervolume(ref_point=np.array(REF_POINT_HV, dtype=float))
        hv_value = float(hv.do(F_feas)) if F_feas is not None and F_feas.shape[0] > 0 else None

        save_run_summary(
            algorithm_name=genetico_norm,
            experiment_id=experiment_id,
            run_id=run_id,
            crossover_name=crossover_name,
            mutation_name=mutation_name,
            pop_size=pop_size,
            n_gen_max=n_gen,
            res=res,
            hv_value=hv_value,
        )

        save_history_csv(res, experiment_id, run_id)

        LOGGER.info(f"[DONE] {experiment_id} hv_feas={hv_value}")
        return res

    except Exception as e:
        # guarda error en csv + log
        LOGGER.exception(f"[FAIL] {experiment_id} ({type(e).__name__}: {e})")
        save_run_error(
            experiment_id=experiment_id,
            run_id=run_id,
            algorithm_name=genetico_norm,
            crossover=crossover_name,
            mutation=mutation_name,
            err=e
        )
        return None

    finally:
        pool.close()
        pool.join()

    

In [ ]:
!nvidia-smi

In [ ]:
# =========================
# EJECUCIÓN DE EXPERIMENTOS (SMSEMOA)
# =========================

import traceback

# Define aquí qué combinaciones quieres probar
CROSSOVERS = ["sbx"]
MUTATIONS  = ["polynomial"]

# Config global
N_RUNS_PER_COMBO = 10
N_GEN = 50
POP_SIZE = 30
N_WORKERS = 4

run_id = 1
resultados_runs = []

for cx in CROSSOVERS:
    for mut in MUTATIONS:
        for k in range(N_RUNS_PER_COMBO):

            try:
                out = ejecutar_experimento(
                    genetico="moead",      # <-- CLAVE
                    n_workers=N_WORKERS,
                    crossover_name=cx,
                    mutation_name=mut,
                    run_id=run_id,
                    n_gen=N_GEN,
                    pop_size=POP_SIZE,
                )
                resultados_runs.append(out)

            except Exception:
                print(f"[ERROR] run_id={run_id} cx={cx} mut={mut} genetico=smsemoa")
                traceback.print_exc()

            run_id += 1

print(f"\nListo. Runs ejecutadas: {len([r for r in resultados_runs if r is not None])}")
print("Archivos generados en ./TFG/SMSEMOA: runs_summary.csv, front_final.csv, history.csv")



Ejecutando: NSGA2_sbx_polynomial_run01 |  pop=30 | n_gen=50


  0%|          | 0/86 [00:00<?, ?it/s]


  0%|          | 0/21 [00:00<?, ?it/s]

  2%|▏         | 1/66 [00:01<01:54,  1.77s/it]

  2%|▏         | 1/57 [00:01<01:47,  1.92s/it]


  3%|▎         | 2/66 [00:03<01:51,  1.74s/it]

  4%|▎         | 2/57 [00:03<01:41,  1.85s/it]


  5%|▍         | 3/66 [00:05<01:49,  1.74s/it]

  5%|▌         | 3/57 [00:05<01:37,  1.81s/it]


  6%|▌         | 4/66 [00:06<01:47,  1.74s/it]

  7%|▋         | 4/57 [00:07<01:36,  1.82s/it]


  8%|▊         | 5/66 [00:08<01:46,  1.75s/it]


 24%|██▍       | 5/21 [00:09<00:29,  1.81s/it]

  9%|▉         | 6/66 [00:10<01:45,  1.76s/it]


 29%|██▊       | 6/21 [00:11<00:27,  1.83s/it]

 11%|█         | 7/66 [00:12<01:44,  1.77s/it]

 12%|█▏        | 7/57 [00:12<01:31,  1.83s/it]


 12%|█▏        | 8/66 [00:14<01:43,  1.78s/it]

 14%|█▍        | 8/57 [00:14<01:28,  1.81s/it]


 14%|█▎        | 9/66 [00:15<01:40,  1.76s/it]

 16%|█▌        | 9/57 [00:16<01:27,  1.83s/it]


 15%|█▌        | 10/66 [00:17<01:40,  1.79s/it

 33%|███▎      | 22/66 [00:39<01:21,  1.85s/it]

 35%|███▍      | 23/66 [00:40<01:13,  1.71s/it]

0: 640x640 1 dog, 942.9ms
Speed: 417.6ms preprocess, 942.9ms inference, 10.7ms postprocess per image at shape (1, 3, 640, 640)




 36%|███▋      | 24/66 [00:42<01:07,  1.61s/it]

 42%|████▏     | 24/57 [00:42<00:52,  1.58s/it]


 38%|███▊      | 25/66 [00:43<01:04,  1.58s/it]

 44%|████▍     | 25/57 [00:44<00:50,  1.58s/it]


 39%|███▉      | 26/66 [00:45<01:05,  1.65s/it]

 31%|███▏      | 27/86 [00:46<01:39,  1.68s/it]


 41%|████      | 27/66 [00:47<01:05,  1.69s/it][A

 47%|████▋     | 27/57 [00:47<00:50,  1.69s/it]


 42%|████▏     | 28/66 [00:49<01:05,  1.71s/it]

 34%|███▎      | 29/86 [00:50<01:38,  1.73s/it]


 44%|████▍     | 29/66 [00:51<01:04,  1.75s/it][A

 35%|███▍      | 30/86 [00:52<01:38,  1.75s/it]


 45%|████▌     | 30/66 [00:52<01:02,  1.74s/it][A

 36%|███▌      | 31/86 [00:53<01:35,  1.74s/it]


 47%|████▋     | 31/66 [00:54<01:00,  1.74s/it][A

 37%|███▋      | 32/86 [00:55<01:34,  1.75s/it]


 48%|████▊     | 32/66 [00:56<01:00,  1.78s/it][A

 38%|███▊      | 33/86 [00:57<01:34,  1.79s/it]


 50%|█████     | 33/66 [00:58<00:58,  1.76s/it][A

 40%|███▉      | 34/86 [00:59<01:32,  1.78s/it

...

0: 640x640 1 tie, 1 vase, 730.7ms
Speed: 707.5ms preprocess, 730.7ms inference, 435.3ms postprocess per image at shape (1, 3, 640, 640)


 23%|██▎       | 21/91 [00:37<02:05,  1.79s/it]

100%|██████████| 29/29 [00:50<00:00,  1.76s/it]



 66%|██████▌   | 25/38 [00:44<00:23,  1.78s/it]

 24%|██▍       | 22/91 [00:39<02:12,  1.92s/it]


  0%|          | 0/7 [00:00<?, ?it/s]

0: 640x640 (no detections), 234.7ms
Speed: 1039.1ms preprocess, 234.7ms inference, 490.0ms postprocess per image at shape (1, 3, 640, 640)


 25%|██▌       | 23/91 [00:41<02:04,  1.83s/it]


 26%|██▋       | 24/91 [00:43<02:08,  1.92s/it]A

  0%|          | 0/10 [00:00<?, ?it/s]


 27%|██▋       | 25/91 [00:46<02:25,  2.21s/it]A

 10%|█         | 1/10 [00:02<00:24,  2.77s/it]


 29%|██▊       | 26/91 [00:49<02:35,  2.40s/it]A

 20%|██        | 2/10 [00:05<00:23,  2.93s/it]


 30%|██▉       | 27/91 [00:52<02:50,  2.67s/it]A

 30%|███       | 3/10 [00:09<00:21,  3.10s/it]


 82%|████████▏ | 31/38 [00:59<00:18,  2.68s/it]

In [ ]:

# =========================
# EJECUCIÓN DE EXPERIMENTOS (copy/paste)
# =========================
# Requisitos: que ya tengas definidos/importados:
# - ejecutar_experimento (la función que te pasé)
# - StableDiffusionProblem
# - get_crossover, get_mutation
# - get_termination_custom
#
# Esto lanza varias runs y te deja los 3 CSVs en ./TFG/
# =========================

import traceback

# Define aquí qué combinaciones quieres probar
CROSSOVERS = ["sbx"]              # añade más si tienes: ["sbx", "ux", ...]
MUTATIONS  = ["polynomial"]       # añade más si tienes: ["polynomial", "gaussian", ...]

# Config global de la corrida
N_RUNS_PER_COMBO = 1
N_GEN = 3
POP_SIZE = 2



# Para reproducibilidad entre sesiones:
# - si BASE_SEED es None, cada run elige una seed random
# - si BASE_SEED es un int, generamos seeds deterministas por run_id
N_WORKERS=4

run_id = 1
resultados_runs = []

for cx in CROSSOVERS:
    for mut in MUTATIONS:
        for k in range(N_RUNS_PER_COMBO):

            try:
                out = ejecutar_experimento(
                    genetico=
                    n_workers=N_WORKERS,
                    crossover_name=cx,
                    mutation_name=mut,
                    run_id=run_id,
                    n_gen=N_GEN,
                    pop_size=POP_SIZE,
        
                )
                resultados_runs.append(out)
            except Exception as e:
                print(f"[ERROR] run_id={run_id} cx={cx} mut={mut}")
                traceback.print_exc()

            run_id += 1

print(f"\nListo. Runs ejecutadas: {len([r for r in resultados_runs if r is not None])}")
print("Archivos generados en ./TFG/: runs_summary.csv, front_final.csv, history.csv")